In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import silhouette_score
import plotly.express as px
from DBSCANSupport import *
from LocalPath import LOCALPATH

Load gravity data

In [2]:
grav = pd.read_csv(LOCALPATH + 'data/test_grav.csv').drop(columns=["old_ind"])


In [3]:
longg = list(grav['Longitude'])
lat = list(grav['Latitude'])
inten = list(grav['Intensity'])
#fig.show()

In [4]:
X = grav[['Longitude', 'Latitude', 'Intensity']].to_numpy()
X

array([[-97.99166667,  -1.50833333,  -5.5733223 ],
       [-97.975     ,  -1.50833333,  -5.16694736],
       [-97.95833333,  -1.50833333,  -4.97332668],
       ...,
       [-90.04166667,  -5.99166667,  -2.35047531],
       [-90.025     ,  -5.99166667,  -0.47824201],
       [-90.00833333,  -5.99166667,  -0.67400765]])

In [5]:
#scale_x = StandardScaler().fit_transform(X)
scale_x = X

In [6]:
test_eps = np.linspace(0.1, 1, 10)
test_samp = np.arange(20, 40)
DBModel_test = DBSCANSupport(LOCALPATH+"data/sample_mask.txt.xlsx", test_zone=(-6, -1.5, -98, -90))

In [7]:
score, params, data_out  = DBModel_test.gridSearch(test_eps, test_samp, scale_x, DBModel_test.outlierDeviation, verbose=True)

Score for 0.1 and 20 is -39.01324503311258
Score for 0.1 and 21 is -39.49006622516556
Score for 0.1 and 22 is -39.920529801324506
Score for 0.1 and 23 is -40.19867549668874
Score for 0.1 and 24 is -40.29801324503311
Score for 0.1 and 25 is -40.29801324503311
0.1 and 26 produced too few clusters
0.1 and 27 produced too few clusters
0.1 and 28 produced too few clusters
0.1 and 29 produced too few clusters
0.1 and 30 produced too few clusters
0.1 and 31 produced too few clusters
0.1 and 32 produced too few clusters
0.1 and 33 produced too few clusters
0.1 and 34 produced too few clusters
0.1 and 35 produced too few clusters
0.1 and 36 produced too few clusters
0.1 and 37 produced too few clusters
0.1 and 38 produced too few clusters
0.1 and 39 produced too few clusters
Score for 0.2 and 20 is 47.602649006622514
Score for 0.2 and 21 is 50.05298013245033
Score for 0.2 and 22 is 50.49006622516556
Score for 0.2 and 23 is 49.45695364238411
Score for 0.2 and 24 is 49.90066225165563
Score for 0.

In [8]:
data_out

array([[-97.99166667,  -1.50833333,  -1.        ,  -5.5733223 ],
       [-97.975     ,  -1.50833333,  -1.        ,  -5.16694736],
       [-97.95833333,  -1.50833333,  -1.        ,  -4.97332668],
       ...,
       [-90.04166667,  -5.99166667,  -1.        ,  -2.35047531],
       [-90.025     ,  -5.99166667,  -1.        ,  -0.47824201],
       [-90.00833333,  -5.99166667,  -1.        ,  -0.67400765]])

In [9]:
cat_mounts = data_out[data_out[:, 2] == -1]

In [10]:
fig = px.scatter(x=cat_mounts[:, 0], y=cat_mounts[:, 1])
fig.show()

In [11]:
test_zone=(-6, -1.5, -98, -90)
seamounts = pd.read_excel(LOCALPATH+"data/sample_mask.txt.xlsx", \
                              sheet_name="new mask")
seamounts = seamounts.drop(columns=["VGG Height", "Radius", "base_depth", "-",
                                        "Name", "Charted", "surface_depth"])
seamounts = seamounts[(seamounts["Latitude"] >= test_zone[0]) & (seamounts["Latitude"] <= test_zone[1]) &
                          (seamounts["Longitude"] >= test_zone[2]) & (seamounts["Longitude"] <= test_zone[3])]
seamounts = seamounts.to_numpy()
fig3 = px.scatter(x=seamounts[:, 0], y=seamounts[:, 1])
fig3.show()

In [12]:
dfout = pd.DataFrame(data_out, columns=["Longitude", "Latitude", "Label", "Intensity"])#.drop(columns=["Score"])
DBModel_test.matchPoints(dfout)
fig = px.scatter(dfout[dfout["Label"] == -1], x="Longitude", y="Latitude", color="True_Seamount")
fig.add_trace(px.scatter(x=seamounts[:, 0], y=seamounts[:, 1]).data[0])
fig.show()


In [13]:
score

51.033112582781456

In [14]:
params

(0.2, 25)

In [15]:
dfout.to_csv(LOCALPATH+"data/DBSCAN_test.csv", index=False)